## Data Breach Analytics 2005 - 2017 (Part III - Unsupervised Topic Modeling, LDA, LSI)
#### by Miriam Rodriguez 

###  Dataset - databreach.csv

### Topic Modeling with Gensim - Text preprocessing

In [19]:
import csv
import pandas as pd

# import packages for text processing
import nltk
from nltk.corpus import stopwords
from nltk.stem.wordnet import WordNetLemmatizer
from nltk.stem.porter import PorterStemmer
import re

import gensim
from gensim.corpora import Dictionary
from gensim.models import ldamodel
from gensim import corpora, models, similarities

from gensim.models.coherencemodel import CoherenceModel
from gensim.models.wrappers import LdaVowpalWabbit, LdaMallet

import numpy
import matplotlib.pyplot as plt
%matplotlib inline

import warnings
warnings.filterwarnings(action= 'ignore')  # To ignore all warnings that arise here to enhance clarity

In [20]:
warnings.filterwarnings(action='ignore')


In [28]:
#import breach data ... open or read the breach data
texts = []
r = csv.reader(open('databreach.csv', 'rb'))
for i in r:
    texts.append(i)  
len(texts)

8177

In [29]:
# Remove useless numbers and alphanumerical words
documents = [re.sub("[^a-zA-Z]+", " ", str(text)) for text in texts]

# tokenize
texts = [[word for word in text.lower().split() ] for text in documents]

# stemming words: having --> have; friends --> friend
lmtzr = WordNetLemmatizer()
texts = [[lmtzr.lemmatize(word) for word in text ] for text in texts]

porter_stemmer = PorterStemmer()
texts = [[porter_stemmer.stem(word) for word in text ] for text in texts]

# remove common words 
stoplist = stopwords.words('english')
texts = [[word for word in text if word not in stoplist] for text in texts]

#remove short words
texts = [[ word for word in tokens if len(word) >= 3 ] for tokens in texts]

In [30]:
# A list of extra stopwords 
extra_stopwords = ['will', 'people', 'need', 'think', 'well','going', 'can', 'country', 'know', 'lot', 'get','make','way','want',
                'like','say','got','said','just','something','tell','put','now', 'bad','back','want','right','every','one','use','come','never', 
                'many','along','things','day','also','first','guy', 'great', 'take', 'good', 'much','anderson', 'let', 'would', 'year', 'thing', 'america',
                'talk', 'talking', 'thank', 'does', 'give', 'look', 'believe', 'tonight','today','see']

extra_stoplist = extra_stopwords
texts = [[word for word in text if word not in extra_stoplist] for text in texts]

In [31]:
# this is text processing required for topic modeling with Gensim

## Create a dictionary representation of the documents.
dictionary = Dictionary(texts)
dictionary.save('databreach.dict')  # store the dictionary, for future reference

len(dictionary)

10721

In [32]:
## Remove rare and common tokens.
# ignore words that appear in less than 2 documents or more than 40% documents (remove too frequent & infrequent words) - an optional step
dictionary.filter_extremes(no_below=2, no_above=0.4) 
len(dictionary)

5091

In [33]:
# convert words to vectors or integers, this is text processing required for topic modeling with Gensim
corpus = [dictionary.doc2bow(text) for text in texts]
corpora.MmCorpus.serialize('databreach.mm', corpus)  # store to disk, for later use  # store to disk, for later use
len(corpus)

8177

In [34]:
print('Number of unique tokens: %d' % len(dictionary))
print('Number of documents: %d' % len(corpus))

Number of unique tokens: 5091
Number of documents: 8177


In [37]:
# later you can retrive the saved dict and corpus
# https://radimrehurek.com/gensim/tut1.html

saved_dict = dictionary.load('databreach.dict')

for i in saved_dict.token2id.iteritems():
    print i

(u'nalleg', 8657)
(u'yellow', 6698)
(u'interchang', 9813)
(u'four', 105)
(u'payoff', 10209)
(u'accret', 547)
(u'lori', 586)
(u'ntulsa', 5239)
(u'hermann', 10084)
(u'lord', 8397)
(u'ncqa', 7143)
(u'digit', 500)
(u'deli', 985)
(u'fradul', 3833)
(u'wjb', 5186)
(u'dell', 8968)
(u'formspr', 3098)
(u'honeywel', 8253)
(u'delt', 8690)
(u'delv', 9384)
(u'oceana', 10651)
(u'broward', 5834)
(u'viewabl', 1582)
(u'kasperski', 7510)
(u'disturb', 8909)
(u'prize', 4142)
(u'cashout', 6295)
(u'carthag', 7985)
(u'voyeur', 9233)
(u'wednesday', 1806)
(u'assail', 7740)
(u'inur', 4172)
(u'bcbsnc', 9148)
(u'terabyt', 4907)
(u'unathor', 10568)
(u'onehitplay', 2978)
(u'charter', 7864)
(u'kuroi', 7422)
(u'miller', 3140)
(u'seper', 8315)
(u'frederick', 7391)
(u'budget', 5479)
(u'second', 672)
(u'nget', 8787)
(u'nsuggest', 1941)
(u'melvin', 9975)
(u'maloney', 7575)
(u'decre', 8514)
(u'launchpoint', 7060)
(u'clorox', 7932)
(u'ongo', 1455)
(u'widget', 4196)
(u'intellectu', 3279)
(u'avert', 8744)
(u'cenabl', 10249)
(

(u'homeport', 2306)
(u'lifestyl', 8677)
(u'abm', 6346)
(u'believ', 39)
(u'airway', 1744)
(u'nfeinstein', 8664)
(u'unreimburs', 5849)
(u'bartholomew', 8948)
(u'pcpa', 9407)
(u'narrest', 9909)
(u'nmention', 10116)
(u'penetr', 2585)
(u'bumper', 9041)
(u'testament', 10425)
(u'resuscit', 8565)
(u'major', 653)
(u'purport', 4170)
(u'guam', 6899)
(u'mockeri', 4910)
(u'number', 14)
(u'precautionari', 2863)
(u'rail', 8184)
(u'guess', 2365)
(u'guest', 1823)
(u'jet', 10068)
(u'arlington', 5415)
(u'evoni', 5465)
(u'swipe', 4647)
(u'nwere', 895)
(u'databreach', 852)
(u'dfr', 4304)
(u'jeb', 6158)
(u'contra', 4123)
(u'saint', 3040)
(u'crow', 8460)
(u'illeg', 1290)
(u'northbound', 9843)
(u'hotl', 3509)
(u'jen', 9404)
(u'relationship', 1525)
(u'ndownload', 10192)
(u'nextbu', 3973)
(u'grace', 4258)
(u'obama', 5639)
(u'reinstal', 9297)
(u'aam', 7149)
(u'depriv', 2982)
(u'aat', 7130)
(u'reus', 3301)
(u'aap', 6673)
(u'torrentfreak', 4774)
(u'reinstat', 6742)
(u'arrang', 2703)
(u'estiamt', 9209)
(u'listen', 

(u'saver', 10551)
(u'nshovel', 8837)
(u'nemerg', 7047)
(u'defraud', 1319)
(u'houstonchronicl', 10193)
(u'jasacar', 8884)
(u'voter', 887)
(u'spew', 4658)
(u'privacyright', 1086)
(u'albuquerqu', 5485)
(u'farber', 9902)
(u'bike', 6959)
(u'hedg', 8244)
(u'worth', 1974)
(u'compassion', 7275)
(u'aurora', 9755)
(u'sheridan', 1985)
(u'kcase', 6140)
(u'aldridg', 8739)
(u'kshb', 8052)
(u'chapel', 9094)
(u'croissant', 3181)
(u'pinch', 9305)
(u'identificaiton', 10684)
(u'upload', 769)
(u'nbeen', 3658)
(u'red', 3800)
(u'nfor', 4238)
(u'nunemploy', 6115)
(u'wholli', 337)
(u'triumph', 9112)
(u'robley', 7200)
(u'jamaica', 8867)
(u'homecar', 6082)
(u'clarifi', 1977)
(u'gasolin', 3299)
(u'envisionrx', 9294)
(u'sunbelt', 5986)
(u'horn', 10718)
(u'consequ', 698)
(u'hors', 1673)
(u'chen', 2656)
(u'panda', 7031)
(u'longstand', 9490)
(u'supervis', 386)
(u'disk', 841)
(u'amus', 8763)
(u'lakeshor', 3564)
(u'near', 2020)
(u'siskiy', 3305)
(u'toll', 1348)
(u'told', 1770)
(u'wilshir', 8045)
(u'umpc', 9575)
(u'mca

(u'hccl', 3038)
(u'medicin', 2624)
(u'engrav', 5533)
(u'metropark', 2619)
(u'intermedi', 7719)
(u'wesleyan', 5311)
(u'nmedicaid', 10535)
(u'glitch', 2244)
(u'purchas', 127)
(u'famili', 411)
(u'asi', 10492)
(u'aggress', 4711)
(u'ash', 9319)
(u'taker', 8842)
(u'injuri', 646)
(u'viru', 149)
(u'taken', 62)
(u'burlington', 7517)
(u'sentara', 3255)
(u'assessor', 10339)
(u'wentworth', 7551)
(u'linden', 2201)
(u'turbo', 2348)
(u'hurri', 1816)
(u'preciou', 9996)
(u'broke', 1893)
(u'alderman', 6665)
(u'grill', 5953)
(u'aspx', 6872)
(u'nwith', 5669)
(u'cquench', 9632)
(u'histori', 413)
(u'kunz', 6735)
(u'ninc', 10078)
(u'nebraska', 2347)
(u'nine', 1263)
(u'landrysinc', 10166)
(u'transcend', 9957)
(u'addreass', 7390)
(u'templat', 3662)
(u'hhc', 9626)
(u'experianidwork', 4984)
(u'anoth', 978)
(u'wfmynew', 9144)
(u'dentrix', 9594)
(u'reject', 2360)
(u'idaho', 4995)
(u'ransom', 1590)
(u'kroll', 3561)
(u'nwithin', 4024)
(u'threat', 1753)
(u'cmug', 10708)
(u'winnebago', 10671)
(u'timesunion', 3416)
(u'

(u'met', 1542)
(u'pedro', 9662)
(u'unpublish', 7180)
(u'scandatafact', 4299)
(u'interpret', 3733)
(u'luther', 8706)
(u'cindi', 9807)
(u'dri', 6970)
(u'jame', 648)
(u'harass', 6918)
(u'sunshin', 6242)
(u'cthey', 4781)
(u'permit', 6076)
(u'serco', 6331)
(u'drc', 8546)
(u'drb', 9333)
(u'drd', 10007)
(u'fell', 2272)
(u'counti', 478)
(u'nineti', 9361)
(u'volunt', 2393)
(u'campaign', 1013)
(u'avenu', 2018)
(u'moral', 6326)
(u'org', 766)
(u'mammogram', 3576)
(u'fiserv', 2406)
(u'reguard', 6429)
(u'landfil', 1217)
(u'poulsbo', 10487)
(u'schneck', 6997)
(u'edward', 8048)
(u'call', 748)
(u'intrust', 3334)
(u'recommend', 419)
(u'partzilla', 6065)
(u'swedishamerican', 6765)
(u'alphabet', 6964)
(u'frenzi', 8728)
(u'kgw', 9448)
(u'warn', 743)
(u'adult', 1626)
(u'accesscatalog', 8022)
(u'wari', 8721)
(u'bujanda', 5171)
(u'ward', 6667)
(u'ware', 9179)
(u'flora', 3859)
(u'room', 1718)
(u'flore', 3890)
(u'nvarieti', 10215)
(u'olen', 9816)
(u'hansel', 4234)
(u'hansen', 10576)
(u'endow', 5563)
(u'defer', 

(u'marriott', 5425)
(u'cabarru', 9042)
(u'allianc', 1458)
(u'road', 5335)
(u'skagit', 10510)
(u'healthitsecur', 1548)
(u'kansan', 7170)
(u'hmsa', 6600)
(u'coupon', 4932)
(u'terminolog', 9660)
(u'mari', 2584)
(u'quietli', 8518)
(u'inbox', 4504)
(u'strip', 1365)
(u'jerusalem', 125)
(u'hutton', 9818)
(u'nmanag', 10503)
(u'complianc', 235)
(u'maass', 6358)
(u'brute', 2738)
(u'compliant', 2104)
(u'amerita', 8131)
(u'newsdetail', 6874)
(u'monadnock', 8213)
(u'alameda', 3168)
(u'mdinr', 6184)
(u'slurper', 2756)
(u'downer', 9320)
(u'daytim', 5094)
(u'enough', 639)
(u'tinley', 6678)
(u'sunris', 9754)
(u'cryptograph', 1357)
(u'woman', 439)
(u'affectedmor', 6206)
(u'possibl', 1025)
(u'mailng', 10590)
(u'vice', 1874)
(u'ember', 7553)
(u'ludlow', 10329)
(u'thedarkoverlord', 8078)
(u'tigta', 5755)
(u'unusu', 1006)
(u'govwin', 10413)
(u'flex', 7826)
(u'neill', 7739)
(u'embed', 1821)
(u'vha', 4003)
(u'proveedor', 9666)
(u'deer', 7855)
(u'casualti', 4183)
(u'fellow', 5363)
(u'grainger', 5023)
(u'deem',

(u'ckimpton', 4276)
(u'protectingourguest', 6556)
(u'immigr', 1788)
(u'wakem', 9059)
(u'blumenth', 5319)
(u'dementia', 5071)
(u'nedlloyd', 8484)
(u'mil', 3070)
(u'colburn', 8535)
(u'min', 3483)
(u'passwordpassword', 10507)
(u'mid', 2035)
(u'npose', 10202)
(u'mix', 3507)
(u'mir', 4404)
(u'micu', 7970)
(u'uppercas', 10508)
(u'analysi', 157)
(u'unless', 2975)
(u'sfx', 6651)
(u'alton', 8240)
(u'salli', 10047)
(u'randstad', 7555)
(u'sfn', 8548)
(u'eight', 460)
(u'nmatter', 5762)
(u'cattl', 7119)
(u'transcript', 2924)
(u'payment', 914)
(u'johnstown', 9467)
(u'zotec', 8871)
(u'wishbon', 4700)
(u'seguro', 204)
(u'request', 420)
(u'nsan', 5238)
(u'expecteda', 2835)
(u'occasion', 4976)
(u'trapwir', 9971)
(u'charley', 9812)
(u'catalina', 1989)
(u'nretir', 3493)
(u'text', 1032)
(u'nnumber', 879)
(u'insync', 3387)
(u'cflash', 10686)
(u'clearanc', 2894)
(u'empir', 4065)
(u'portfolio', 4845)
(u'texa', 935)
(u'urogynecolog', 9378)
(u'staff', 206)
(u'wear', 3028)
(u'cmail', 7789)
(u'bicycl', 5872)
(u'r

(u'serf', 4470)
(u'ubiqu', 3912)
(u'naccess', 1553)
(u'balanc', 695)
(u'posit', 352)
(u'driveway', 1165)
(u'pre', 3551)
(u'rene', 1430)
(u'prc', 3429)
(u'cdigniti', 1997)
(u'anm', 9720)
(u'ann', 7748)
(u'ninvolv', 1239)
(u'pri', 532)
(u'hershey', 9579)
(u'reno', 8150)
(u'mateo', 2183)
(u'cjacket', 10011)
(u'homedepot', 6459)
(u'rent', 3759)
(u'techniqu', 2370)
(u'moreov', 1635)
(u'bridgewat', 5376)
(u'dinclud', 9011)
(u'hingham', 7525)
(u'ideal', 961)
(u'nazareth', 9612)
(u'publicintegr', 10468)
(u'nsell', 7531)
(u'bradi', 6132)
(u'surf', 10499)
(u'surg', 10102)
(u'sure', 4026)
(u'mcpn', 5167)
(u'ukrainian', 6320)
(u'greenplum', 3075)
(u'cigarett', 2491)
(u'lur', 9963)
(u'nvulner', 4022)
(u'fcc', 5580)
(u'connor', 9341)
(u'freshman', 6923)
(u'librarian', 6576)
(u'intermedix', 6047)
(u'icon', 8946)
(u'feinstein', 8660)
(u'disenrol', 8686)
(u'later', 144)
(u'intelenet', 9484)
(u'tweet', 4663)
(u'senior', 2256)
(u'recipi', 544)
(u'unaccompani', 10179)
(u'cheap', 10594)
(u'trespass', 7984)

(u'safekeep', 9054)
(u'providencenightlif', 9686)
(u'buffalo', 7808)
(u'scroll', 6473)
(u'mardi', 8181)
(u'trustco', 7496)
(u'edg', 6783)
(u'edd', 3381)
(u'ganz', 8988)
(u'miner', 8070)
(u'edm', 9153)
(u'alien', 6363)
(u'nembarrass', 8904)
(u'gang', 2495)
(u'edt', 9429)
(u'edu', 3061)
(u'issuer', 4875)
(u'broadridg', 8262)
(u'theorist', 10216)
(u'simon', 9676)
(u'bpgwi', 6494)
(u'gold', 10301)
(u'prequalif', 9982)
(u'susquehanna', 9591)
(u'newenglandcalendar', 8866)
(u'outgo', 7793)
(u'breach', 42)
(u'cybercrim', 4287)
(u'sniper', 6003)
(u'imposs', 3932)
(u'religi', 5553)
(u'carefirst', 7420)
(u'divisadero', 2931)
(u'heard', 4583)
(u'lifega', 6420)
(u'electron', 171)
(u'spoof', 3911)
(u'goldthwait', 7542)
(u'relev', 1333)
(u'weapon', 6247)
(u'kmtv', 8125)
(u'misplac', 739)
(u'happenedth', 4832)
(u'aprehend', 3837)
(u'inacit', 9555)
(u'prep', 6063)
(u'watersid', 9789)
(u'pleas', 297)
(u'cfo', 7897)
(u'cfm', 6165)
(u'edina', 7865)
(u'locatd', 9814)
(u'bellin', 10666)
(u'battl', 3214)
(u'

In [38]:
# you can retrieve the saved corpus

corpus_saved = corpora.MmCorpus('databreach.mm')

In [39]:
numpy.random.seed(1) # setting random seed to get the same results each time. 
model = ldamodel.LdaModel(corpus, id2word=dictionary, num_topics=35, passes=50)

# Optimal k value

In [ ]:
numpy.random.seed(1) # setting random seed to get the same results each time.
k_range = range(2,35)
scores = []
for k in k_range:
    goodLdaModel = ldamodel.LdaModel(corpus=corpus, id2word=dictionary, num_topics=k, passes=50)
    goodcm = CoherenceModel(model=goodLdaModel, corpus=corpus, dictionary=dictionary, coherence='u_mass')
    scores.append(goodcm.get_coherence())
    
plt.figure()
plt.plot(k_range, scores)

In [ ]:
print goodcm.get_coherence()

In [43]:
model.save('lda.model') # same for tfidf, lda, ...
#model = models.LdaModel.load('data/lda.model')

# Prints the topics (Term-Topic Distribution)

In [44]:
# print words without probability
for i in range(0,35):
    topics = model.show_topic(i, 10)
    print ', '.join([str(word[0]) for word in topics])
  

email, employe, sent, includ, person, contain, spreadsheet, account, social, phish
card, payment, system, affect, date, point, malwar, locat, credit, restaur
card, credit, custom, debit, bank, may, account, purchas, affect, store
network, bar, list, soni, gang, seek, intrus, facebook, download, automat
updat, million, lawsuit, boe, prescript, file, claim, action, class, five
laptop, stolen, contain, comput, social, employe, person, drive, address, offic
investig, thi, data, washington, gener, attorney, law, incid, hotel, forens
ephi, devic, electron, comput, encrypt, drive, portabl, health, contain, laptop
mail, sent, address, letter, error, social, receiv, client, print, form
access, unauthor, may, address, parti, includ, account, third, thi, investig
server, comput, network, system, access, viru, hacker, technolog, group, malwar
research, data, center, offici, agenc, ani, test, state, taxpay, googl
data, compani, com, http, www, servic, accord, notifi, custom, thi
record, document, f

# Assign the topics to the documents in corpus (Document-Topic Distribution)

In [45]:
lda_corpus = model[corpus]

results = []
for i in lda_corpus:
#    print i
    results.append(i)
print 

In [46]:
# finding highest value from each row
toptopic = [max(collection, key=lambda x: x[1])[0] for collection in results]
# toptopic

In [47]:
toptopic = pd.DataFrame(toptopic)
documents = pd.DataFrame(documents)
documents = documents.rename(columns = {0: 'documents'})
summary = documents.join(toptopic)
summary.head(10)

documents   0
0   An external auditor lost a CD with names Soci...  25
1   There are TennCare r r n enrollees at risk of...   5
2   A laptop computer was stolen from a vehicle x...   5
3   A Fidelity laptop used by a former Fidelity e...  16
4   A former contract worker of a Japanese commer...  12
5   Patient names addresses Social Security numbe...  27
6   At least colleges are scrambling to inform te...   5
7   Hundreds of files with Social Security number...  28
8   A computer was compromised by a virus That ca...  22
9   N r r nLocation of breached information Other...  21

# pyLDAvis


In [48]:
import pyLDAvis.gensim

In [49]:
pyLDAvis.enable_notebook()
pyLDAvis.gensim.prepare(model, corpus, dictionary)

C:\Users\DOUGR\Anaconda2\lib\site-packages\pyLDAvis\_prepare.py:387: DeprecationWarning: 
.ix is deprecated. Please use
.loc for label based indexing or
.iloc for positional indexing

See the documentation here:
http://pandas.pydata.org/pandas-docs/stable/indexing.html#ix-indexer-is-deprecated
  topic_term_dists = topic_term_dists.ix[topic_order]


PreparedData(topic_coordinates=            Freq  cluster  topics         x         y
topic                                                
32     11.972906        1       1  0.036645  0.266956
9       7.105825        1       2 -0.151273  0.056178
27      6.708659        1       3 -0.146317  0.134811
12      6.390792        1       4 -0.047429 -0.026586
5       5.862791        1       5 -0.189147  0.139269
25      4.199461        1       6 -0.235657  0.026562
20      4.008282        1       7  0.047162  0.113005
7       3.943294        1       8  0.004434  0.266137
2       3.840249        1       9 -0.047807 -0.074956
18      3.667372        1      10 -0.070683 -0.073478
23      3.392467        1      11 -0.078684 -0.036330
22      2.959613        1      12 -0.135394  0.014348
0       2.701649        1      13 -0.163444  0.055301
21      2.592651        1      14  0.299787  0.261118
6       2.457245        1      15 -0.011352 -0.026547
13      2.284916        1      16 -0.117070  0.001449
33      2.039403        1      17 -0.162715 -0.021410
26      2.022424        1      18 -0.002885 -0.110322
28      2.018943        1      19  0.001114 -0.071329
30      1.938635        1      20  0.080962  0.068805
8       1.865252        1      21 -0.062124 -0.027142
10      1.820170        1      22  0.104403  0.001012
1       1.731527        1      23  0.026993 -0.028161
31      1.474641        1      24  0.009030 -0.115225
16      1.433485        1      25 -0.102220 -0.002884
4       1.332329        1      26  0.064556 -0.131518
11      1.248045        1      27  0.031845 -0.098525
29      1.192501        1      28 -0.055522 -0.022565
19      1.151465        1      29  0.059311 -0.067700
34      0.911348        1      30  0.338417  0.173844
15      0.854615        1      31  0.109951 -0.129871
3       0.838285        1      32  0.173198 -0.134851
17      0.824151        1      33  0.122830 -0.148360
24      0.686258        1      34  0.104082 -0.068371
14      0.528340        1      35  0.165003 -0.162663, topic_info=     Category         Freq       Term        Total  loglift  logprob
term                                                                
2761  Default  2993.000000     associ  2993.000000  30.0000  30.0000
4677  Default  2370.000000    present  2370.000000  29.0000  29.0000
3882  Default  2327.000000      nbusi  2327.000000  28.0000  28.0000
1673  Default  2462.000000       card  2462.000000  27.0000  27.0000
3998  Default  3829.000000    employe  3829.000000  26.0000  26.0000
3565  Default  2924.000000    patient  2924.000000  25.0000  25.0000
2887  Default  2780.000000     health  2780.000000  24.0000  24.0000
939   Default  1876.000000     credit  1876.000000  23.0000  23.0000
905   Default  2191.000000     laptop  2191.000000  22.0000  22.0000
3633  Default  1916.000000     custom  1916.000000  21.0000  21.0000
2794  Default   977.000000     member   977.000000  20.0000  20.0000
1336  Default  3197.000000    address  3197.000000  19.0000  19.0000
4529  Default  1904.000000      email  1904.000000  18.0000  18.0000
865   Default  3527.000000     social  3527.000000  17.0000  17.0000
3025  Default  2392.000000     comput  2392.000000  16.0000  16.0000
1997  Default  1500.000000     nlocat  1500.000000  15.0000  15.0000
810   Default  1736.000000     servic  1736.000000  14.0000  14.0000
3122  Default  2573.000000     access  2573.000000  13.0000  13.0000
4885  Default   793.000000      paper   793.000000  12.0000  12.0000
2107  Default  2644.000000    contain  2644.000000  11.0000  11.0000
4714  Default   992.000000    student   992.000000  10.0000  10.0000
2098  Default  1889.000000      medic  1889.000000   9.0000   9.0000
3537  Default  1123.000000     server  1123.000000   8.0000   8.0000
41    Default  2728.000000     affect  2728.000000   7.0000   7.0000
4423  Default  1142.000000      locat  1142.000000   6.0000   6.0000
38    Default  1768.000000     stolen  1768.000000   5.0000   5.0000
2398  Default  1421.000000 

### get_term_topics

The function `get_term_topics` returns the odds of that particular word belonging to a particular topic. 


In [50]:
model.get_term_topics('hack')

[(19, 0.010074164), (23, 0.013244809), (30, 0.01502259)]

In [55]:
model.get_term_topics('password')

[(23, 0.07222867)]

In [56]:
summary.groupby(0).count()

documents
0            
0         174
1          80
2         355
3           2
4          14
5         884
6          40
7         118
8         105
9         534
10         27
11         17
12        419
13        197
14          3
15          7
16         87
17         10
18        288
19         15
20         66
21       1266
22        396
23        296
24          8
25        442
26         49
27        696
28         62
29         52
30        224
31         40
32        780
33        150
34        274

### Here are the 35 topics

In [57]:
model.show_topics(num_topics=35)
#show_topics(num_topics=35, num_words=10, log=False, formatted=True)

[(0,
  u'0.108*"email" + 0.098*"employe" + 0.037*"sent" + 0.030*"includ" + 0.027*"person" + 0.027*"contain" + 0.026*"spreadsheet" + 0.024*"account" + 0.022*"social" + 0.016*"phish"'),
 (1,
  u'0.088*"card" + 0.087*"payment" + 0.037*"system" + 0.027*"affect" + 0.024*"date" + 0.024*"point" + 0.023*"malwar" + 0.023*"locat" + 0.023*"credit" + 0.021*"restaur"'),
 (2,
  u'0.164*"card" + 0.134*"credit" + 0.115*"custom" + 0.027*"debit" + 0.026*"bank" + 0.020*"may" + 0.019*"account" + 0.017*"purchas" + 0.017*"affect" + 0.015*"store"'),
 (3,
  u'0.031*"network" + 0.023*"bar" + 0.021*"list" + 0.020*"soni" + 0.018*"gang" + 0.016*"seek" + 0.015*"intrus" + 0.015*"facebook" + 0.014*"download" + 0.014*"automat"'),
 (4,
  u'0.092*"updat" + 0.051*"million" + 0.040*"lawsuit" + 0.038*"boe" + 0.037*"prescript" + 0.032*"file" + 0.030*"claim" + 0.026*"action" + 0.023*"class" + 0.023*"five"'),
 (5,
  u'0.097*"laptop" + 0.072*"stolen" + 0.069*"contain" + 0.052*"comput" + 0.042*"social" + 0.035*"employe" + 0.03

## Apply topic model to new data to determine how breaches occurred


In [72]:
unlabeled = [] 

In [76]:
# Remove useless numbers and alphanumerical words
unlabeled = [re.sub("[^a-zA-Z]+", " ", text) for text in unlabeled]
# tokenize
unlabeled = [[word for word in text.lower().split() ] for text in unlabeled]
# stemming words: having --> have; friends --> friend
lmtzr = WordNetLemmatizer()
unlabeled = [[lmtzr.lemmatize(word) for word in text ] for text in unlabeled]
# remove common words 
stoplist = stopwords.words('english')
unlabeled = [[word for word in text if word not in stoplist] for text in unlabeled]
#remove short words
unlabeled = [[ word for word in tokens if len(word) >= 3 ] for tokens in unlabeled]

In [77]:
unlabeled

[]

## Results

### LSI and Results

In [58]:
tfidf = models.TfidfModel(corpus)

In [59]:
corpus_tfidf = tfidf[corpus]


In [60]:
for doc in corpus_tfidf:
    print(doc)

[(0, 0.054436636896890787), (1, 0.21778874225475314), (2, 0.071567874369151366), (3, 0.32327270743129993), (4, 0.214010470303582), (5, 0.25026541800794805), (6, 0.15768733172955074), (7, 0.2754249562985957), (8, 0.13188581052092682), (9, 0.18378888396835491), (10, 0.13303659623879602), (11, 0.64591811494302354), (12, 0.12339022719209709), (13, 0.11210403307592905), (14, 0.074172392655797101), (15, 0.035832988006378498), (16, 0.24470792840626038), (17, 0.14907641529648277), (18, 0.1334770868933732), (19, 0.10118790670216064)]
[(10, 0.4234211923190167), (14, 0.11803580301731009), (15, 0.057023581987845663), (20, 0.069964610900259849), (21, 0.38168569943017039), (22, 0.38543246893940231), (23, 0.4032120176626699), (24, 0.17613697909134216), (25, 0.072795034409568207), (26, 0.096710948730237806), (27, 0.19335290693224602), (28, 0.48888884808961092), (29, 0.14049627227181308)]
[(30, 0.31336177523400194), (31, 0.38320258138222013), (32, 0.34362947069350258), (33, 0.79804696999305813)]
[(0, 0

[(1, 0.47389290185816224), (4, 0.058208956159889115), (30, 0.12951271145198368), (31, 0.23756697181628175), (32, 0.071011188986103951), (46, 0.12513925010427898), (102, 0.20771275662250696), (103, 0.080557608611511552), (105, 0.21581522401420328), (122, 0.062587895359464768), (124, 0.15636817847722437), (138, 0.28444834512589789), (152, 0.15895586781403501), (184, 0.11136718561896974), (320, 0.096002224834958086), (327, 0.17402623547287413), (339, 0.22870892749054816), (377, 0.18053946960758202), (386, 0.14348709858604669), (420, 0.19711901150484085), (425, 0.18482679647708886), (426, 0.2793383596134858), (427, 0.2304332167943732), (428, 0.15785834151770631), (429, 0.077765548018908517), (430, 0.23421954437668807)]
[(0, 0.049649599415629339), (20, 0.040098803615715189), (22, 0.44180566947350619), (25, 0.041721003682129582), (43, 0.070416847005428107), (69, 0.14262725861415326), (112, 0.1314294276776887), (114, 0.19532396299148386), (116, 0.096126051518943559), (127, 0.13056434072676071

[(2, 0.066358248094219946), (3, 0.049956796749257133), (4, 0.024804006001900941), (7, 0.04256266689140787), (15, 0.033224604322039303), (19, 0.093822155209503363), (24, 0.10262563719754574), (25, 0.042413789708662122), (29, 0.040929847724643476), (30, 0.027593984535244993), (35, 0.063830755118374521), (48, 0.060688542310770865), (63, 0.033960510976865713), (67, 0.068214440577395188), (85, 0.028354048330629752), (87, 0.023934708778029314), (91, 0.091312501817138916), (98, 0.023193070648192489), (99, 0.038624839168093235), (116, 0.097722244788536347), (118, 0.071870740706135861), (121, 0.1060576788255973), (122, 0.026669959995129888), (160, 0.097788743758826985), (219, 0.09980565479518369), (318, 0.075308703534624308), (332, 0.051312818598772868), (341, 0.16943919876257441), (342, 0.099251623663748872), (362, 0.20850053910923352), (367, 0.066454236695578719), (370, 0.15716890710135303), (388, 0.044203921582569534), (428, 0.067266611682575389), (429, 0.033137462807335066), (437, 0.0755634

[(53, 0.11496268764130513), (63, 0.20978173651349802), (85, 0.058383117380449254), (87, 0.14785009488874476), (91, 0.12534620452848522), (98, 0.047756276291724853), (131, 0.07623473922107106), (132, 0.10359893960459887), (161, 0.18220305998703759), (185, 0.10136886484734799), (189, 0.063392985209097488), (200, 0.2483580283729368), (353, 0.10427232897788373), (401, 0.094796340629867581), (420, 0.17295484574083592), (429, 0.068232527440569013), (438, 0.17811214778599357), (441, 0.11714101748732773), (442, 0.11979811662631076), (483, 0.14923561948637951), (505, 0.11006270903619314), (508, 0.1401540696530858), (612, 0.13454400975978686), (630, 0.14515228786132989), (700, 0.19125612671831527), (866, 0.14126902885578232), (869, 0.12798469180424105), (918, 0.17596239738790653), (976, 0.14654268106724727), (1090, 0.12870738148769525), (1094, 0.21939828520249458), (1178, 0.17923565215198003), (1199, 0.15000532478354098), (1540, 0.22483328747325682), (1578, 0.3082949933095081), (1579, 0.17062245

[(15, 0.038706258783398804), (25, 0.049411547675200972), (26, 0.065645104678595453), (69, 0.084459060986290344), (90, 0.11731282759893473), (98, 0.054039288822777372), (99, 0.089994933021108225), (112, 0.077828082482135186), (114, 0.11566427527721287), (122, 0.12428071236708467), (147, 0.14370414548640939), (421, 0.4701886928190242), (422, 0.27592940261947269), (424, 0.19463379147987669), (450, 0.162239143447033), (482, 0.18074689213224454), (546, 0.20092381934656944), (720, 0.21824278265594133), (1702, 0.20281663324864474), (1812, 0.23000152241819863), (2029, 0.3104169206072146), (2030, 0.34885555323239376), (2031, 0.33184618732838633)]
[(2, 0.27481093001164442), (19, 0.38854783646806823), (25, 0.17564919704640328), (30, 0.22855119809946067), (32, 0.2506270178315026), (63, 0.28128288112645466), (69, 0.30023682607660324), (138, 0.33464416656911411), (607, 0.58852222533492515)]
[(0, 0.21301280779036294), (4, 0.20935795162295304), (15, 0.070107980781533602), (20, 0.086018405462995814), (

...

[(4, 0.14678000374498706), (15, 0.098304837259773653), (25, 0.12549376523694214), (30, 0.32657992044607392), (31, 0.199683366691874), (32, 0.17906217999660101), (91, 0.36023346007513501), (98, 0.13724714452732129), (167, 0.16597813537850811), (391, 0.35762412723912157), (511, 0.28953409686807802), (654, 0.4480231771196419), (1039, 0.43110150307095535)]
[(3, 0.11085331112164989), (4, 0.11007936350254016), (7, 0.094445858463704319), (15, 0.03686242553031089), (25, 0.094115502441466492), (26, 0.062517997313707344), (70, 0.13283408343614453), (83, 0.16109988585860074), (85, 0.062917167346209737), (87, 0.053110725495353589), (100, 0.14805274998897441), (159, 0.24799887254796976), (172, 0.10241111307831285), (232, 0.1747636227879252), (393, 0.31043551872643532), (429, 0.073531485471358599), (450, 0.1545106277743056), (479, 0.12922555532420821), (511, 0.10856972435732527), (623, 0.19135249855522679), (627, 0.32330956432926145), (631, 0.11675164856949105), (648, 0.12860995159155875), (875, 0.2

[(2, 0.10212985390574927), (4, 0.15270020424014932), (63, 0.10453506909065007), (105, 0.14153762135237882), (112, 0.10281885210403402), (121, 0.16322997600330877), (122, 0.16418752430638966), (189, 0.09476692583678524), (320, 0.12592185384272969), (400, 0.087969351828479911), (418, 0.17511549708616719), (428, 0.20705577441169937), (442, 0.17908762611928386), (568, 0.25052563629818175), (618, 0.18172301542160202), (712, 0.2234749974104403), (719, 0.15667373827089492), (820, 0.38404460802486862), (898, 0.27425636008729665), (1040, 0.35713748387964156), (5044, 0.46087384385585872)]
[(29, 0.21390665433802208), (31, 0.17635224383685638), (91, 0.15907178460034926), (103, 0.17940012782278952), (134, 0.22280785659243127), (167, 0.14658515171683836), (189, 0.16089893309953493), (191, 0.20618609147872755), (374, 0.22354779637727973), (400, 0.14935775039318494), (549, 0.32667463592538126), (559, 0.28778431381865499), (751, 0.29570472907155465), (2272, 0.61389339583502212)]
[(4, 0.1102769844274249

[(31, 0.37597094675244086), (143, 0.22430071325539275), (144, 0.24006391794534113), (146, 0.23564779049294568), (718, 0.41677772780834588), (938, 0.53254695311059241), (939, 0.48771358367720041)]
[(143, 0.38628063722589812), (144, 0.41342732197773152), (146, 0.4058220651703679), (718, 0.71775592659868237)]
[(140, 0.507644438004063), (143, 0.25748156406221684), (144, 0.27557662287542461), (146, 0.27050721677752165), (179, 0.54588167812936528), (718, 0.47843174310463199)]
[(140, 0.507644438004063), (143, 0.25748156406221684), (144, 0.27557662287542461), (146, 0.27050721677752165), (179, 0.54588167812936528), (718, 0.47843174310463199)]
[(0, 0.09250585404514905), (2, 0.060808746811950962), (4, 0.090918646239733086), (8, 0.11205881033561672), (12, 0.10484040710349116), (14, 0.18906514767415439), (15, 0.0304460501922461), (25, 0.038866749406454244), (29, 0.075013817236574826), (30, 0.050572631657006005), (31, 0.12368811086665091), (33, 0.12879469880559122), (38, 0.094748222555663439), (47, 

[(13, 0.091790756780326749), (15, 0.058680084856145953), (20, 0.035998521676782406), (30, 0.0487354894689674), (43, 0.063216409587395189), (52, 0.415466092102239), (53, 0.098608787508608922), (58, 0.10764179905765622), (75, 0.11260109547696452), (128, 0.1451847560970761), (131, 0.065390043977397991), (136, 0.062127963669782967), (179, 0.075380061473781443), (355, 0.21325009294008948), (393, 0.12354302734535273), (400, 0.15142436736041109), (408, 0.14167125650777471), (441, 0.10047724125927547), (456, 0.13219026180610283), (526, 0.086888911239108801), (552, 0.1141123499521131), (559, 0.097255432100715078), (593, 0.10325245258658095), (611, 0.12354302734535273), (638, 0.15524126382367565), (719, 0.089895784560353451), (822, 0.12888962212763211), (855, 0.094254785707325039), (862, 0.16272402879829698), (904, 0.16543196640571203), (1424, 0.14269163450277111), (1554, 0.15093104562471321), (2059, 0.16762587433951495), (2206, 0.17832537261401865), (2651, 0.48479475858301663), (2974, 0.1794034

[(0, 0.055704458836096475), (25, 0.04680895635746507), (30, 0.060906871407204501), (32, 0.066789881974679097), (47, 0.13715555943268012), (61, 0.11454100086288437), (91, 0.13436645461484528), (98, 0.051192946408423694), (102, 0.097682567335742584), (103, 0.15153761676566593), (132, 0.11105419800217427), (143, 0.04443498802103741), (144, 0.0475577503226155), (145, 0.061519150550274161), (146, 0.046682895456580657), (158, 0.088814694064140109), (163, 0.18308059866766693), (165, 0.089225571924179459), (167, 0.061909556068837628), (169, 0.105019087148776), (177, 0.19137916309666855), (178, 0.10347881801901475), (180, 0.087212389731289905), (182, 0.079974080882103685), (187, 0.070765891913829593), (189, 0.067954914965630608), (192, 0.13908010078712535), (207, 0.10334766058748762), (233, 0.10964868416285203), (245, 0.13283929216171905), (263, 0.090912929105309473), (286, 0.10556913974560583), (287, 0.14368051165241277), (290, 0.12522869770595838), (333, 0.14648690078225329), (337, 0.11568532

In [61]:
lsi = models.LsiModel(corpus_tfidf, id2word=dictionary, num_topics=35) # initialize an LSI transformation
corpus_lsi = lsi[corpus_tfidf] # create a double wrapper over the original corpus: bow->tfidf->fold-in-lsi

In [62]:
lsi.print_topics(35)


[(0,
  u'0.445*"nbusi" + 0.437*"present" + 0.420*"locat" + 0.419*"associ" + 0.264*"nlocat" + 0.163*"film" + 0.163*"network" + 0.158*"paper" + 0.156*"server" + 0.139*"email"'),
 (1,
  u'-0.205*"locat" + 0.194*"laptop" + 0.169*"patient" + 0.169*"employe" + 0.165*"health" + 0.137*"individu" + 0.135*"comput" + 0.131*"report" + 0.128*"stolen" + 0.124*"contain"'),
 (2,
  u'-0.444*"locat" + 0.410*"film" + 0.404*"nlocat" + 0.398*"paper" + -0.355*"network" + -0.351*"server" + -0.120*"email" + 0.082*"laptop" + 0.061*"nbusi" + 0.059*"present"'),
 (3,
  u'-0.415*"film" + -0.388*"paper" + 0.322*"nlocat" + -0.290*"locat" + -0.274*"human" + 0.251*"laptop" + -0.178*"servic" + -0.167*"ocrport" + -0.167*"jsf" + -0.167*"report"'),
 (4,
  u'0.348*"human" + -0.274*"locat" + 0.273*"nlocat" + -0.234*"paper" + -0.228*"film" + 0.215*"ocrport" + 0.214*"jsf" + 0.204*"jsessionid" + 0.200*"servic" + 0.181*"report"'),
 (5,
  u'-0.512*"server" + -0.501*"network" + 0.299*"locat" + 0.260*"email" + 0.207*"electron" + -